In [1]:
import re
import os
from collections import Counter
import string
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
import nltk
import pandas as pd
import numpy as np
import chardet

In [40]:
nltk.download('punkt')
nltk.download('stopwords')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data] Error downloading 'punkt' from
[nltk_data]     <https://raw.githubusercontent.com/nltk/nltk_data/gh-
[nltk_data]     pages/packages/tokenizers/punkt.zip>:   <urlopen error
[nltk_data]     [Errno -3] Temporary failure in name resolution>
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

By building a preprocessing text function we can ensure all text being used will be all in a uniform manner. Some of the text, when scraped, gets their spaces excluded. We can use a dictionary-based approach or natural language processing (**NLP**) techniques. However, for a simple regex-based fix, we can try adding spaces based on common English word patterns.

In [41]:
import re

def fix_spacing(text):
    """
    Fixes missing spaces in a text:
    - Adds spaces before uppercase letters following lowercase letters.
    - Splits improperly joined words.
    - Handles cases where words are merged without uppercase hints.
    """
    words = text.split()  # Split into words based on existing spaces
    fixed_words = []

    for word in words:
        if len(word) > 8:
            # Fix missing spaces before uppercase letters (e.g., "sinnersNor" → "sinners Nor")
            word = re.sub(r'(?<=[a-z])(?=[A-Z])', ' ', word)

            # Handle common merging issues (heuristic approach)
            word = re.sub(r'(\w)([A-Z][a-z])', r'\1 \2', word)  # "sinnersNor" → "sinners Nor"
            word = re.sub(r'([a-z])([A-Z])', r'\1 \2', word)  # "NorSitsIn" → "Nor Sits In"

            # Attempt to split words that might be missing spaces (fallback)
            word = re.sub(r'([a-z])([A-Za-z]{2,})', r'\1 \2', word)

        # Store the processed word
        fixed_words.append(word)

    # Rejoin the words into a corrected sentence
    return ' '.join(fixed_words)

# Example Test
text = "Blessed is the man Who walks not in the counsel of the ungodly Nor stands in the way of sinnersNorsitsintheseatofthetroublesome"
print(fix_spacing(text))


Blessed is the man Who walks not in the counsel of the ungodly Nor stands in the way of s inners No rsitsintheseatofthetroublesome


In [42]:
def preprocess_text(text):
    # Tokenize text
    tokens = word_tokenize(text)
    # Convert to lowercase
    tokens = [word.lower() for word in tokens]
    # Remove punctuation
    tokens = [word for word in tokens if word not in string.punctuation]
    # Remove stopwords
    stop_words = set(stopwords.words('english'))
    tokens = [word for word in tokens if word not in stop_words]
    return tokens

After doing some preprocessing, the Psalms will be the easiest to access within a csv file. The following few code cels is going to work at putting the psalms in a CSV file. Since I am going to do this we are also going to separate the psalms by verse as well.

Creating a data frame to start to load the psalms into by their verses.

In [43]:
psalms_df = pd.DataFrame(columns=["tradition", "text", "psalm_num", "verse_num", "verse"])
psalms_df

Empty DataFrame
Columns: [tradition, text, psalm_num, verse_num, verse]
Index: []

In [44]:
def organize_psalms(directory, trad, text, debug=True):
    psalm_num = 1
    for filename in os.listdir(directory):
        if filename.endswith('.txt'):
            # Read a small part of the file to detect encoding, different file are being endcoded in a different way
            with open(os.path.join(directory, filename), 'rb') as file:
                raw_data = file.read(10000)  # Read first 10KB
                detected = chardet.detect(raw_data)
                encoding = detected['encoding']

            with open(os.path.join(directory, filename), 'r', encoding=encoding, errors="replace") as file:
                # While reading in a file, I am removing all line breaks
                psalm = file.read().replace("\n", " ").replace("\r", " ")
                # Handling words that are lacking their spaces.
                #psalm = add_missing_spaces(psalm)
                psalms_to_df(psalm, trad, text, psalm_num)
                # Debug statement to see if the code works for inputing the first psalm.
                #break
            psalm_num += 1

            if debug:
                break

In [45]:
def psalms_to_df(psalm, tradition, text, psalm_num):
    global psalms_df  # If you're using a global variable, declare it
    if 'psalms_df' not in globals():
        psalms_df = pd.DataFrame(columns=["tradition", "text", "psalm_num", "verse_num", "verse"])

    verses = psalm.split("[NEXT VERSE]")
    # Setting the verse number back to 1 incase it is something else.
    num = 1
    for verse in verses:
        new_verse = pd.DataFrame([{"tradition": tradition, "text": text, "psalm_num": psalm_num, "verse_num": num,
                                  "verse": verse}])
        
        # Adding the data of the new target verse to the existing psalms dataframe.
        psalms_df = pd.concat([psalms_df, new_verse])
        
        # incrementing the verse number
        num += 1
        
    # droping possible duplicates incase I have added the same data twice
    psalms_df.drop_duplicates()

    '''
    # Iterating through each verse to prefrom tasks on each verse.
        print(f"Verse {num}: {verse}.")
        num += 1
    '''

Splitting up psalms by verse and adding them to a data to further clean and gather data on them.
# Implementation
## Psalms from the Orthodox Bible

In [46]:
import os

os.getcwd()

'/opt/notebooks/website/scripts/cleaning'

In [47]:
organize_psalms("../../data/psalms/bible", "Orthodox", "Bible", debug=False)
# the above should give us 2722 rows of data
psalms_df

tradition   text psalm_num verse_num  \
0   Orthodox  Bible         1         1   
0   Orthodox  Bible         1         2   
0   Orthodox  Bible         1         3   
0   Orthodox  Bible         1         4   
0   Orthodox  Bible         1         5   
..       ...    ...       ...       ...   
0   Orthodox  Bible       155         3   
0   Orthodox  Bible       155         4   
0   Orthodox  Bible       155         5   
0   Orthodox  Bible       155         6   
0   Orthodox  Bible       155         7   

                                                verse  
0   PSALM 152 1Alleluia Praise God in His saints P...  
0    2 Praise Him for His mighty acts Praise Him a...  
0    3 Praise Him with the sound of a trumpet Prai...  
0    4 Praise Him with timbrel and dance Praise Hi...  
0    5 Praise Him with resounding cymbals Praise H...  
..                                                ...  
0    3 And whoshall tell my Lord The Lord Himself ...  
0    4 He sent forth His Angel And took me from my...  
0    5 My brothers were handsome and tall But the ...  
0    6 I went out to meet the foreigner And he cur...  
0    7 But I drew his own sword and beheaded him A...  

[2738 rows x 5 columns]

In [48]:
# Display all rows and columns
with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    display(psalms_df)

tradition   text psalm_num verse_num  \
0  Orthodox  Bible         1         1   
0  Orthodox  Bible         1         2   
0  Orthodox  Bible         1         3   
0  Orthodox  Bible         1         4   
0  Orthodox  Bible         1         5   
0  Orthodox  Bible         1         6   
0  Orthodox  Bible         2         1   
0  Orthodox  Bible         2         2   
0  Orthodox  Bible         2         3   
0  Orthodox  Bible         2         4   
0  Orthodox  Bible         2         5   
0  Orthodox  Bible         2         6   
0  Orthodox  Bible         2         7   
0  Orthodox  Bible         3         1   
0  Orthodox  Bible         4         1   
0  Orthodox  Bible         4         2   
0  Orthodox  Bible         5         1   
0  Orthodox  Bible         5         2   
0  Orthodox  Bible         5         3   
0  Orthodox  Bible         5         4   
0  Orthodox  Bible         5         5   
0  Orthodox  Bible         5         6   
0  Orthodox  Bible         6         1   
0  Orthodox  Bible         6         2   
0  Orthodox  Bible         6         3   
0  Orthodox  Bible         6         4   
0  Orthodox  Bible         6         5   
0  Orthodox  Bible         6         6   
0  Orthodox  Bible         6         7   
0  Orthodox  Bible         6         8   
0  Orthodox  Bible         6         9   
0  Orthodox  Bible         6        10   
0  Orthodox  Bible         6        11   
0  Orthodox  Bible         6        12   
0  Orthodox  Bible         7         1   
0  Orthodox  Bible         7         2   
0  Orthodox  Bible         7         3   
0  Orthodox  Bible         7         4   
0  Orthodox  Bible         7         5   
0  Orthodox  Bible         7         6   
0  Orthodox  Bible         7         7   
0  Orthodox  Bible         7         8   
0  Orthodox  Bible         7         9   
0  Orthodox  Bible         8         1   
0  Orthodox  Bible         8         2   
0  Orthodox  Bible         8         3   
0  Orthodox  Bible         8         4   
0  Orthodox  Bible         8         5   
0  Orthodox  Bible         8         6   
0  Orthodox  Bible         8         7   
0  Orthodox  Bible         8         8   
0  Orthodox  Bible         8         9   
0  Orthodox  Bible         9         1   
0  Orthodox  Bible         9         2   
0  Orthodox  Bible         9         3   
0  Orthodox  Bible         9         4   
0  Orthodox  Bible         9         5   
0  Orthodox  Bible         9         6   
0  Orthodox  Bible         9         7   
0  Orthodox  Bible         9         8   
0  Orthodox  Bible         9         9   
0  Orthodox  Bible         9        10   
0  Orthodox  Bible         9        11   
0  Orthodox  Bible         9        12   
0  Orthodox  Bible         9        13   
0  Orthodox  Bible        10         1   
0  Orthodox  Bible        10         2   
0  Orthodox  Bible        10         3   
0  Orthodox  Bible        10         4   
0  Orthodox  Bible        10         5   
0  Orthodox  Bible        10         6   
0  Orthodox  Bible        10         7   
0  Orthodox  Bible        10         8   
0  Orthodox  Bible        10         9   
0  Orthodox  Bible        10        10   
0  Orthodox  Bible        10        11   
0  Orthodox  Bible        11         1   
0  Orthodox  Bible        11         2   
0  Orthodox  Bible        11         3   
0  Orthodox  Bible        11         4   
0  Orthodox  Bible        11         5   
0  Orthodox  Bible        11         6   
0  Orthodox  Bible        11         7   
0  Orthodox  Bible        11         8   
0  Orthodox  Bible        11         9   
0  Orthodox  Bible        11        10   
0  Orthodox  Bible        11        11   
0  Orthodox  Bible        11        12   
0  Orthodox  Bible        11        13   
0  Orthodox  Bible        11        14   
0  Orthodox  Bible        11        15   
0  Orthodox  Bible        11        16   
0  Orthodox  Bible        11        17   
0  Orthodox  Bible        12         1   
0  Orthodox 

In [49]:
psalms_df = psalms_df.iloc[16:].reset_index(drop=True)


In [50]:
psalms_df

tradition   text psalm_num verse_num  \
0     Orthodox  Bible         5         1   
1     Orthodox  Bible         5         2   
2     Orthodox  Bible         5         3   
3     Orthodox  Bible         5         4   
4     Orthodox  Bible         5         5   
...        ...    ...       ...       ...   
2717  Orthodox  Bible       155         3   
2718  Orthodox  Bible       155         4   
2719  Orthodox  Bible       155         5   
2720  Orthodox  Bible       155         6   
2721  Orthodox  Bible       155         7   

                                                  verse  
0     PSALM 1 Blessed is the man Who walks not in th...  
1      2 But his will is in the law of the Lord And ...  
2      3 He shall be like a tree Planted by streams ...  
3      4 Not so are the ungodly not so But they are ...  
4      5 Therefore the ungodly shall not rise in the...  
...                                                 ...  
2717   3 And whoshall tell my Lord The Lord Himself ...  
2718   4 He sent forth His Angel And took me from my...  
2719   5 My brothers were handsome and tall But the ...  
2720   6 I went out to meet the foreigner And he cur...  
2721   7 But I drew his own sword and beheaded him A...  

[2722 rows x 5 columns]

Resetting the psalm numbering

In [51]:
psalms_df['psalm_num'] = psalms_df['psalm_num'] - 4


psalms_df

tradition   text psalm_num verse_num  \
0     Orthodox  Bible         1         1   
1     Orthodox  Bible         1         2   
2     Orthodox  Bible         1         3   
3     Orthodox  Bible         1         4   
4     Orthodox  Bible         1         5   
...        ...    ...       ...       ...   
2717  Orthodox  Bible       151         3   
2718  Orthodox  Bible       151         4   
2719  Orthodox  Bible       151         5   
2720  Orthodox  Bible       151         6   
2721  Orthodox  Bible       151         7   

                                                  verse  
0     PSALM 1 Blessed is the man Who walks not in th...  
1      2 But his will is in the law of the Lord And ...  
2      3 He shall be like a tree Planted by streams ...  
3      4 Not so are the ungodly not so But they are ...  
4      5 Therefore the ungodly shall not rise in the...  
...                                                 ...  
2717   3 And whoshall tell my Lord The Lord Himself ...  
2718   4 He sent forth His Angel And took me from my...  
2719   5 My brothers were handsome and tall But the ...  
2720   6 I went out to meet the foreigner And he cur...  
2721   7 But I drew his own sword and beheaded him A...  

[2722 rows x 5 columns]

## Psalms from and Orthodox Psalter 
<INSERT_LINK>

In [57]:
organize_psalms("../../data/psalms/psalter", "Orthodox", "Psalter", debug=False)
#psalms_df

In [58]:
# Display all rows and columns
with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    display(psalms_df)

tradition     text psalm_num verse_num  \
0     Orthodox    Bible         1         2   
1     Orthodox    Bible         1         3   
2     Orthodox    Bible         1         4   
3     Orthodox    Bible         1         5   
4     Orthodox    Bible         1         6   
5     Orthodox    Bible         2         1   
6     Orthodox    Bible         2         2   
7     Orthodox    Bible         2         3   
8     Orthodox    Bible         2         4   
9     Orthodox    Bible         2         5   
10    Orthodox    Bible         2         6   
11    Orthodox    Bible         2         7   
12    Orthodox    Bible         2         8   
13    Orthodox    Bible         2         9   
14    Orthodox    Bible         2        10   
15    Orthodox    Bible         2        11   
16    Orthodox    Bible         2        12   
17    Orthodox    Bible         3         1   
18    Orthodox    Bible         3         2   
19    Orthodox    Bible         3         3   
20    Orthodox    Bible         3         4   
21    Orthodox    Bible         3         5   
22    Orthodox    Bible         3         6   
23    Orthodox    Bible         3         7   
24    Orthodox    Bible         3         8   
25    Orthodox    Bible         3         9   
26    Orthodox    Bible         4         1   
27    Orthodox    Bible         4         2   
28    Orthodox    Bible         4         3   
29    Orthodox    Bible         4         4   
30    Orthodox    Bible         4         5   
31    Orthodox    Bible         4         6   
32    Orthodox    Bible         4         7   
33    Orthodox    Bible         4         8   
34    Orthodox    Bible         4         9   
35    Orthodox    Bible         5         1   
36    Orthodox    Bible         5         2   
37    Orthodox    Bible         5         3   
38    Orthodox    Bible         5         4   
39    Orthodox    Bible         5         5   
40    Orthodox    Bible         5         6   
41    Orthodox    Bible         5         7   
42    Orthodox    Bible         5         8   
43    Orthodox    Bible         5         9   
44    Orthodox    Bible         5        10   
45    Orthodox    Bible         5        11   
46    Orthodox    Bible         5        12   
47    Orthodox    Bible         5        13   
48    Orthodox    Bible         6         1   
49    Orthodox    Bible         6         2   
50    Orthodox    Bible         6         3   
51    Orthodox    Bible         6         4   
52    Orthodox    Bible         6         5   
53    Orthodox    Bible         6         6   
54    Orthodox    Bible         6         7   
55    Orthodox    Bible         6         8   
56    Orthodox    Bible         6         9   
57    Orthodox    Bible         6        10   
58    Orthodox    Bible         6        11   
59    Orthodox    Bible         7         1   
60    Orthodox    Bible         7         2   
61    Orthodox    Bible         7         3   
62    Orthodox    Bible         7         4   
63    Orthodox    Bible         7         5   
64    Orthodox    Bible         7         6   
65    Orthodox    Bible         7         7   
66    Orthodox    Bible         7         8   
67    Orthodox    Bible         7         9   
68    Orthodox    Bible         7        10   
69    Orthodox    Bible         7        11   
70    Orthodox    Bible         7        12   
71    Orthodox    Bible         7        13   
72    Orthodox    Bible         7        14   
73    Orthodox    Bible         7        15   
74    Orthodox    Bible         7        16   
75    Orthodox    Bible         7        17   
76    Orthodox    Bible         8         1   
77    Orthodox    Bible         8         2   
78    Orthodox    Bible         8         3   
79    Orthodox    Bible         8         4   
80    Orthodox    Bible         8         5   
81    Orthodox    Bible         8         6   
82    Orthodox    Bible         8         7   
83    Orthodox    Bible         8         8   
84    Orth

In [56]:
# Display all rows and columns
with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    display(psalms_df)

tradition   text psalm_num verse_num  \
0     Orthodox  Bible         1         2   
1     Orthodox  Bible         1         3   
2     Orthodox  Bible         1         4   
3     Orthodox  Bible         1         5   
4     Orthodox  Bible         1         6   
5     Orthodox  Bible         2         1   
6     Orthodox  Bible         2         2   
7     Orthodox  Bible         2         3   
8     Orthodox  Bible         2         4   
9     Orthodox  Bible         2         5   
10    Orthodox  Bible         2         6   
11    Orthodox  Bible         2         7   
12    Orthodox  Bible         2         8   
13    Orthodox  Bible         2         9   
14    Orthodox  Bible         2        10   
15    Orthodox  Bible         2        11   
16    Orthodox  Bible         2        12   
17    Orthodox  Bible         3         1   
18    Orthodox  Bible         3         2   
19    Orthodox  Bible         3         3   
20    Orthodox  Bible         3         4   
21    Orthodox  Bible         3         5   
22    Orthodox  Bible         3         6   
23    Orthodox  Bible         3         7   
24    Orthodox  Bible         3         8   
25    Orthodox  Bible         3         9   
26    Orthodox  Bible         4         1   
27    Orthodox  Bible         4         2   
28    Orthodox  Bible         4         3   
29    Orthodox  Bible         4         4   
30    Orthodox  Bible         4         5   
31    Orthodox  Bible         4         6   
32    Orthodox  Bible         4         7   
33    Orthodox  Bible         4         8   
34    Orthodox  Bible         4         9   
35    Orthodox  Bible         5         1   
36    Orthodox  Bible         5         2   
37    Orthodox  Bible         5         3   
38    Orthodox  Bible         5         4   
39    Orthodox  Bible         5         5   
40    Orthodox  Bible         5         6   
41    Orthodox  Bible         5         7   
42    Orthodox  Bible         5         8   
43    Orthodox  Bible         5         9   
44    Orthodox  Bible         5        10   
45    Orthodox  Bible         5        11   
46    Orthodox  Bible         5        12   
47    Orthodox  Bible         5        13   
48    Orthodox  Bible         6         1   
49    Orthodox  Bible         6         2   
50    Orthodox  Bible         6         3   
51    Orthodox  Bible         6         4   
52    Orthodox  Bible         6         5   
53    Orthodox  Bible         6         6   
54    Orthodox  Bible         6         7   
55    Orthodox  Bible         6         8   
56    Orthodox  Bible         6         9   
57    Orthodox  Bible         6        10   
58    Orthodox  Bible         6        11   
59    Orthodox  Bible         7         1   
60    Orthodox  Bible         7         2   
61    Orthodox  Bible         7         3   
62    Orthodox  Bible         7         4   
63    Orthodox  Bible         7         5   
64    Orthodox  Bible         7         6   
65    Orthodox  Bible         7         7   
66    Orthodox  Bible         7         8   
67    Orthodox  Bible         7         9   
68    Orthodox  Bible         7        10   
69    Orthodox  Bible         7        11   
70    Orthodox  Bible         7        12   
71    Orthodox  Bible         7        13   
72    Orthodox  Bible         7        14   
73    Orthodox  Bible         7        15   
74    Orthodox  Bible         7        16   
75    Orthodox  Bible         7        17   
76    Orthodox  Bible         8         1   
77    Orthodox  Bible         8         2   
78    Orthodox  Bible         8         3   
79    Orthodox  Bible         8         4   
80    Orthodox  Bible         8         5   
81    Orthodox  Bible         8         6   
82    Orthodox  Bible         8         7   
83    Orthodox  Bible         8         8   
84    Orthodox  Bible         8         9   
85    Orthodox  Bible         8        10   
86    Orthodox  Bible         9         1   
87    Orthodox  Bible         9         2   


# Psalms, by verse, to CSV

In [54]:
# converting the file to a csv to do further steramline cleaning in another notebook or file. 
psalms_df.to_csv("../../data/csv/psalm_verse.csv", index=False)

In [31]:
'''import spacy

def add_spaces(text):
   nlp = spacy.load('en_core_web_sm')
   doc = nlp(text)
   words = []
   for token in doc:
      if not token.is_space:
         words.append(token.text)
      else:
         words.append(' ')
   return ''.join(words)

# Example usage
input_text = "Thisisatestsentencewithnospaces."
output_text = add_spaces(input_text)
print(output_text)
'''

'import spacy\n\ndef add_spaces(text):\n   nlp = spacy.load(\'en_core_web_sm\')\n   doc = nlp(text)\n   words = []\n   for token in doc:\n      if not token.is_space:\n         words.append(token.text)\n      else:\n         words.append(\' \')\n   return \'\'.join(words)\n\n# Example usage\ninput_text = "Thisisatestsentencewithnospaces."\noutput_text = add_spaces(input_text)\nprint(output_text)\n'

In [30]:
#spacy.load('en_core_web_sm')

# Playground Stuff

In [29]:
def analyze_psalms(directory):
    all_words = []
    for filename in os.listdir(directory):
        if filename.endswith('.txt'):
            with open(os.path.join(directory, filename), 'r', encoding='utf-8') as file:
                text = file.read()
                tokens = preprocess_text(text)
                all_words.extend(tokens)


    # Counting word frequencies
    word_counts = Counter(all_words)

    # Returnig the 20 most common word
    return word_counts.most_common(20)